In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/ml-for-oceanography/sample2.csv
/kaggle/input/ml-for-oceanography/test1.csv
/kaggle/input/ml-for-oceanography/train.csv


In [2]:
train_data=pd.read_csv('/kaggle/input/ml-for-oceanography/train.csv')
train_data.head()
test_data=pd.read_csv('/kaggle/input/ml-for-oceanography/test1.csv')

In [3]:
train_data.head()

ID   #YY  MM  DD  hh  mm  WDIR(degT)  WSPD(m/s)  GST(m/s)  \
0  2017424150  2017   4  24   1  50          23        3.0       3.6   
1  2017424250  2017   4  24   2  50          30        2.9       3.3   
2  2017424350  2017   4  24   3  50         360        2.2       2.5   
3  2017424450  2017   4  24   4  50         355        2.5       3.1   
4  2017424550  2017   4  24   5  50         355        3.5       4.5   

   DPD(sec)  APD(sec)  MWD(degT)  PRES(hPa)  ATMP(degC)  WTMP(degC)  \
0      4.17      3.33        349     1019.1         4.7         5.1   
1      5.26      4.21        358     1018.8         4.6         4.8   
2      5.88      4.79         11     1018.3         4.6         4.7   
3      5.88      4.95         23     1018.1         4.6         4.6   
4      6.25      4.98         26     1018.3         4.5         4.6   

   DEWP(degC)  WVHT(m)  
0         4.2     0.39  
1         4.1     0.65  
2         4.2     0.90  
3         4.2     0.91  
4         4.0     0.88

In [4]:
train_data.shape

(3886, 17)

In [5]:
X=train_data.iloc[:,[2,4,*range(6, 16)]]
X.head()

MM  hh  WDIR(degT)  WSPD(m/s)  GST(m/s)  DPD(sec)  APD(sec)  MWD(degT)  \
0   4   1          23        3.0       3.6      4.17      3.33        349   
1   4   2          30        2.9       3.3      5.26      4.21        358   
2   4   3         360        2.2       2.5      5.88      4.79         11   
3   4   4         355        2.5       3.1      5.88      4.95         23   
4   4   5         355        3.5       4.5      6.25      4.98         26   

   PRES(hPa)  ATMP(degC)  WTMP(degC)  DEWP(degC)  
0     1019.1         4.7         5.1         4.2  
1     1018.8         4.6         4.8         4.1  
2     1018.3         4.6         4.7         4.2  
3     1018.1         4.6         4.6         4.2  
4     1018.3         4.5         4.6         4.0

In [6]:
y=train_data.iloc[:,-1]
y.head()

0    0.39
1    0.65
2    0.90
3    0.91
4    0.88
Name: WVHT(m), dtype: float64

using gridsearchCV for hyperparamater testing

In [7]:
from catboost import CatBoostRegressor
from sklearn.model_selection import GridSearchCV
model=CatBoostRegressor()
param_grid = {'iterations': [500, 1000, 1500],
              'learning_rate': [0.01, 0.05, 0.1],
              'depth': [4, 6, 8]}
# Instantiate the CatBoostRegressor
model = CatBoostRegressor()

# Instantiate GridSearchCV with the CatBoostRegressor and the parameter grid
grid_search = GridSearchCV(model, param_grid=param_grid, cv=5)

# Fit GridSearchCV to the training data
grid_search.fit(X, y)

# Print the best hyperparameters and the corresponding score
print('Best Hyperparameters: ', grid_search.best_params_)
print('Best Score: ', grid_search.best_score_)

0:	learn: 0.3538570	total: 58.2ms	remaining: 29.1s
1:	learn: 0.3511729	total: 60.4ms	remaining: 15s
2:	learn: 0.3483467	total: 62ms	remaining: 10.3s
3:	learn: 0.3456926	total: 63.4ms	remaining: 7.86s
4:	learn: 0.3428725	total: 64.6ms	remaining: 6.39s
5:	learn: 0.3401953	total: 65.8ms	remaining: 5.42s
6:	learn: 0.3376745	total: 67ms	remaining: 4.72s
7:	learn: 0.3350500	total: 68.2ms	remaining: 4.19s
8:	learn: 0.3324912	total: 69.3ms	remaining: 3.78s
9:	learn: 0.3298772	total: 70.5ms	remaining: 3.45s
10:	learn: 0.3273747	total: 71.7ms	remaining: 3.19s
11:	learn: 0.3248310	total: 72.8ms	remaining: 2.96s
12:	learn: 0.3223690	total: 74ms	remaining: 2.77s
13:	learn: 0.3200308	total: 75.1ms	remaining: 2.61s
14:	learn: 0.3175827	total: 76.2ms	remaining: 2.46s
15:	learn: 0.3152499	total: 77.4ms	remaining: 2.34s
16:	learn: 0.3128090	total: 78.5ms	remaining: 2.23s
17:	learn: 0.3103761	total: 79.8ms	remaining: 2.14s
18:	learn: 0.3079493	total: 81.1ms	remaining: 2.05s
19:	learn: 0.3057078	total: 82

In [8]:
X_test=test_data.iloc[:,[2,4,*range(6, 16)]]
X_test.head()

MM  hh  WDIR(degT)  WSPD(m/s)  GST(m/s)  DPD(sec)  APD(sec)  MWD(degT)  \
0   7  22         340        6.7       8.2      2.35      2.37        177   
1   7  23          15        2.3       5.5      2.60      2.44        336   
2   7   1          11        1.6       2.7      3.13      2.95        341   
3   7  10          21        4.1       4.9      2.86      2.59          8   
4   7  11          16        4.5       5.4      2.74      2.64         16   

   PRES(hPa)  ATMP(degC)  WTMP(degC)  DEWP(degC)  
0     1011.5        18.6        16.8        17.8  
1     1010.7        19.0        16.9        17.8  
2     1010.6        17.9        16.7        17.3  
3     1015.8        20.0        20.3        19.5  
4     1016.5        20.1        20.3        19.6

predictions

In [9]:
pred=grid_search.predict(X_test)

In [10]:
pred

array([0.32370083, 0.26985507, 0.28046561, ..., 0.68439814, 1.29539968,
       1.28436258])

In [11]:
output=pd.DataFrame({'Id':test_data.ID,'WVHT(m)':pred})
output.to_csv('submission.csv',index=False)
print("Your submission was successful")

Your submission was successful
